### Imports

In [1]:
import pandas as pd
from datetime import timedelta
from datetime import datetime as dt
import datetime
import yfinance as yf
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.model_selection import train_test_split, cross_val_score, StratifiedKFold
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import RandomizedSearchCV
from imblearn.over_sampling import ADASYN
from xgboost import XGBClassifier
import xgboost as xgb
import pytz
from sklearn.preprocessing import MinMaxScaler
from imblearn.over_sampling import BorderlineSMOTE
from sklearn.decomposition import PCA
from sklearn.metrics import roc_auc_score
from sklearn.feature_selection import SelectFromModel
import tensorflow as tf
from tensorflow import keras
from keras import layers, callbacks
from sklearn.utils.class_weight import compute_class_weight
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.pipeline import Pipeline
from tensorflow.keras.optimizers.legacy import Adam
from tensorflow.keras.layers import Dense, BatchNormalization, Dropout
from tensorflow.keras.regularizers import l2
from sklearn.ensemble import VotingClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.tree import DecisionTreeClassifier
from keras.models import Sequential
import keras_tuner as kt
from kerastuner.tuners import RandomSearch
import joblib
import itertools

/var/folders/zc/z8rbpqpj3s38f0x8wmhkq0lh0000gn/T/ipykernel_25571/3193444192.py:39: DeprecationWarning: `import kerastuner` is deprecated, please use `import keras_tuner`.
  from kerastuner.tuners import RandomSearch


### Helper Functions

In [2]:
def next_four_fridays():
    # Get today's date and time in EST timezone
    est = pytz.timezone('US/Eastern')
    today = dt.now(est)
    
    # Find the next Friday
    days_until_friday = (4 - today.weekday() + 7) % 7
    next_friday = today + timedelta(days=days_until_friday)
    
    # Reset the time to 4:30 PM on the next Friday
    next_friday = next_friday.replace(hour=16, minute=30, second=0, microsecond=0)
    
    # If today is Friday and it's past 4:30 PM, consider the next week's Friday
    if today.weekday() == 4 and today.time() > next_friday.time():
        next_friday += timedelta(days=7)
    
    # Remove time from datetime for output
    next_friday = next_friday.date()
    
    # Find the Friday after the next
    following_friday = next_friday + timedelta(days=7)
    
    # Find the Friday after the following
    next_next_friday = following_friday + timedelta(days=7)
    
    # Find the Friday after the next next
    next_next_next_friday = next_next_friday + timedelta(days=7)
    
    return next_friday.strftime('%Y-%m-%d'), following_friday.strftime('%Y-%m-%d'), next_next_friday.strftime('%Y-%m-%d'), next_next_next_friday.strftime('%Y-%m-%d')

# Get the next four Fridays
friday1, friday2, friday3, friday4 = next_four_fridays()
print(f"The next four Fridays are: {friday1}, {friday2}, {friday3}, and {friday4}")

The next four Fridays are: 2023-09-22, 2023-09-29, 2023-10-06, and 2023-10-13


### Assuming Profits

In [3]:
# Initialize the variables
initial_amount = 1327  # Starting amount in dollars
roi_rate = 5

# Number of weeks for which the ROI is to be calculated
weeks = 38

# Initialize a variable to hold the current amount
current_amount = initial_amount

# Loop through each week to calculate and print the ROI
for week in range(1, weeks + 1):
    # Calculate the number of $100 chunks in the current amount
    chunks = current_amount // 100  # Use integer division to get whole chunks
    
    # Calculate the ROI for this week
    weekly_roi = chunks * (roi_rate)  # 1% of each $100 chunk is $1
    
    # Print the details for this week
    print(f"Week {week}: {current_amount} +{weekly_roi}")
    
    # Update the current amount for the next week
    current_amount += weekly_roi


Week 1: 1327 +65
Week 2: 1392 +65
Week 3: 1457 +70
Week 4: 1527 +75
Week 5: 1602 +80
Week 6: 1682 +80
Week 7: 1762 +85
Week 8: 1847 +90
Week 9: 1937 +95
Week 10: 2032 +100
Week 11: 2132 +105
Week 12: 2237 +110
Week 13: 2347 +115
Week 14: 2462 +120
Week 15: 2582 +125
Week 16: 2707 +135
Week 17: 2842 +140
Week 18: 2982 +145
Week 19: 3127 +155
Week 20: 3282 +160
Week 21: 3442 +170
Week 22: 3612 +180
Week 23: 3792 +185
Week 24: 3977 +195
Week 25: 4172 +205
Week 26: 4377 +215
Week 27: 4592 +225
Week 28: 4817 +240
Week 29: 5057 +250
Week 30: 5307 +265
Week 31: 5572 +275
Week 32: 5847 +290
Week 33: 6137 +305
Week 34: 6442 +320
Week 35: 6762 +335
Week 36: 7097 +350
Week 37: 7447 +370
Week 38: 7817 +390


# Viewing option chains

In [4]:
print(friday1)

2023-09-22


In [5]:
file_viewer = pd.read_csv('naked_puts_results.csv')
filtered_data = file_viewer[file_viewer['Expiration Date'] == friday1]

# Display all rows, no limit
pd.set_option('display.max_rows', None)
# Display all columns, no limit
pd.set_option('display.max_columns', None)

filtered_data['ROI (%)'] = filtered_data['ROI (%)'].astype(float)
# filter out rows with ROI (%) greater than 0.8
# filtered_data = filtered_data[filtered_data['ROI (%)'] > 0.8]
# filter out rows with strike price less than 6
# filtered_data = filtered_data[filtered_data['strike'] <= 7]

# sort by ROI (%) in ascending order
filtered_data = filtered_data.sort_values(by=['ROI (%)'], ascending=False)

# Show only the columns 'Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)', 'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', and '52WeekLow'
filtered_data = filtered_data[['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)',
    'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', '52WeekLow']]

# Show only the top 10 rows
filtered_data.head(20)

Expiration Date   ETF  Stock Price   bid  strike  ROI (%)  OTM (%)  \
112      2023-09-22    WE         4.31  0.75     1.0   300.00    76.80   
92       2023-09-22  SFIX         3.23  0.19     3.0     6.76     7.12   
90       2023-09-22   RUM         6.79  0.40     6.5     6.56     4.27   
62       2023-09-22  NKLA         1.19  0.06     1.0     6.38    15.97   
114      2023-09-22    WE         4.31  0.20     3.5     6.06    18.79   
69       2023-09-22  NVAX         7.71  0.30     7.5     4.17     2.72   
28       2023-09-22  EOSE         2.59  0.10     2.5     4.17     3.47   
19       2023-09-22   CGC         1.35  0.04     1.0     4.17    25.93   
10       2023-09-22   AMC         8.36  0.30     8.0     3.90     4.31   
56       2023-09-22  LUMN         1.54  0.05     1.5     3.45     2.60   
113      2023-09-22    WE         4.31  0.10     3.0     3.45    30.39   
80       2023-09-22  PTON         5.04  0.16     5.0     3.31     0.79   
120      2023-09-22    WW        11.37  0.35    11.0     3.29     3.25   
101      2023-09-22  SPCE         2.05  0.06     2.0     3.09     2.44   
12       2023-09-22  APLD         5.26  0.15     5.0     3.09     4.94   
26       2023-09-22  DISH         6.54  0.19     6.5     3.01     0.61   
22       2023-09-22  CHPT         5.62  0.16     5.5     3.00     2.14   
77       2023-09-22  PLUG         8.52  0.23     8.5     2.78     0.23   
14       2023-09-22  AVXL         7.57  0.20     7.5     2.74     0.92   
89       2023-09-22   RUM         6.79  0.15     6.0     2.56    11.63   

     Implied Volatility   volume  openInterest  highPrice  \
112               25.06      1.0          27.0       0.75   
92                 1.64    750.0         740.0       0.19   
90                 1.43    930.0         131.0       0.40   
62                 2.19  29482.0       15265.0       0.06   
114                2.73    147.0         290.0       0.20   
69                 0.96    561.0         490.0       0.30   
28                 1.11    461.0        2304.0       0.10   
19                 2.38   5426.0       13158.0       0.04   
10                 0.97  14087.0        3608.0       0.30   
56                 0.81    139.0        1485.0       0.05   
113                2.58     74.0         360.0       0.10   
80                 0.63    517.0        1196.0       0.16   
120                0.86    502.0         700.0       0.35   
101                0.73    498.0         882.0       0.06   
12                 1.03     14.0         292.0       0.15   
26                 0.55    133.0         573.0       0.19   
22                 0.69   2399.0       44965.0       0.16   
77                 0.50   1534.0        1338.0       0.23   
14                 0.64     55.0         178.0       0.20   
89                 1.24    320.0         423.0       0.15   

     Original Stock Price  Original ROI (%)  Original OTM (%)  50-day MA  \
112                  4.31            300.00             76.80       7.38   
92                   3.23              6.76              7.12       4.14   
90                   6.79              6.56              4.27       7.85   
62                   1.19              6.38             15.97       1.81   
114                  4.31              6.06             18.79       7.38   
69                   7.71              4.17              2.72       8.19   
28                   2.59              4.17              3.47       3.07   
19                   1.35              4.17             25.93       0.56   
10                   8.36              3.90              4.31      33.18   
56                   1.54              3.45              2.60       1.71   
113                  4.31              3.45             30.39       7.38   
80                   5.04              3.31              0.79       7.55   
120                 11.37              3.29              3.25       9.78   
101                  2.05              3.09              2.44       3.17   
12                   5.26  

In [6]:
# Read in data
df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Define function to color rows 
def color_row(row):
    color = 'lightgreen' if row['Status'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Filter columns to keep
columns = ['ETF', 'Original Stock Price', 'Stock Price', 'strike', 'volume',  
           'openInterest', 'highPrice', 'Original ROI (%)', 'Original OTM (%)',
           '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP',
           '52WeekHigh', '52WeekLow', 'Status']

# Take top 100 rows ordered by Original ROI (%)
df = df[columns].sort_values('Original ROI (%)', ascending=False).head(100)

# Style DataFrame 
styled_df = (df.style  
             .applymap(lambda x: 'color: black') # Set text color
             .apply(color_row, axis=1) # Set row colors
             .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns))

# Display DataFrame 
styled_df

In [7]:
# Load your dataset
data = pd.read_csv("Data/putsDataSuccessFailed.csv")

# Preprocessing Steps
# -------------------
# 1. Fill missing values with median
# Fill missing values with median only for numeric columns
for col in data.select_dtypes(include=['float64']).columns:
    data[col].fillna(data[col].median(), inplace=True)

# 2. Label Encode 'Status' column
label_encoder = LabelEncoder()
data['Status'] = label_encoder.fit_transform(data['Status'])

# Save the label encoder to a file
label_encoder_filename = "label_encoder.joblib"
joblib.dump(label_encoder, label_encoder_filename)

# 3. Feature selection
# selected_columns = ['strike', 'volume', 'openInterest', 'Implied Volatility', 'Original Stock Price', 'Original ROI (%)', 'Original OTM (%)', 'Original Implied Volatility', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', 'Delta', 'Gamma', 'Theta', 'Vega', 'Rho', '52WeekHigh', '52WeekLow', 'targetHighPrice', 'targetLowPrice', 'targetMeanPrice', 'targetMedianPrice', 'recommendationMean']
selected_columns = ['Original ROI (%)', 'Delta', 'openInterest', 'Gamma', 'Original OTM (%)', 'VWAP', 'MACD', '200-day MA', '52WeekHigh', 'volume']
X = data[selected_columns]
y = data['Status']

# 4. Feature Scaling
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# Split the data
X_train, X_test, y_train, y_test = train_test_split(X_scaled, y, test_size=0.3, random_state=42)

# Apply SMOTE to the training data
smote = SMOTE(random_state=42)
X_train_balanced, y_train_balanced = smote.fit_resample(X_train, y_train)

# Initialize the model
random_forest_model = RandomForestClassifier(random_state=42)

rf_param_grid = {
    'n_estimators': [50, 100, 150, 200],
    'max_depth': [None, 10, 20, 30, 40],
    'min_samples_split': [2, 5, 10, 15],
    'min_samples_leaf': [1, 2, 4, 8],
    'max_features': ['auto', 'sqrt', 'log2', None, 0.25, 0.5, 0.75],  # Include valid options
    'bootstrap': [True, False],
    'criterion': ['gini', 'entropy']
}

rf_grid_search = GridSearchCV(estimator=random_forest_model, param_grid=rf_param_grid,
                              cv=3, n_jobs=-1, verbose=2, scoring='accuracy')

rf_grid_search.fit(X_train_balanced, y_train_balanced)

# Get the best parameters and update the model
best_params = rf_grid_search.best_params_
random_forest_model = RandomForestClassifier(**best_params, random_state=42)

# Train the model with best parameters
random_forest_model.fit(X_train_balanced, y_train_balanced)

# Save the trained model and scaler to separate files
model_filename = "random_forest_model.joblib"
scaler_filename = "scaler.joblib"

joblib.dump(random_forest_model, model_filename)
joblib.dump(scaler, scaler_filename)

print(f"Random Forest model saved to {model_filename}")
print(f"Scaler saved to {scaler_filename}")

# Evaluate the model
y_pred = random_forest_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
print(f"Model Accuracy with Best Parameters: {accuracy * 100:.2f}%")

# Making Predictions on New Data
# ------------------------------
# Load new data
new_data = pd.read_csv("naked_puts_results.csv")

# Apply the same preprocessing steps
for col in new_data.select_dtypes(include=['float64']).columns:
    new_data[col].fillna(new_data[col].median(), inplace=True)

new_X = new_data[selected_columns]
new_X_scaled = scaler.transform(new_X)

# Make predictions
new_predictions = random_forest_model.predict(new_X_scaled)

# Convert numerical predictions back to labels ("Success" or "Failed")
new_predictions_labels = label_encoder.inverse_transform(new_predictions)

# Add predictions to the new data
new_data["Guess"] = new_predictions_labels

# Save the new data with predictions
new_data.to_csv("Data/new_data_with_predictions.csv", index=False)

Fitting 3 folds for each of 8960 candidates, totalling 26880 fits
[CV] END bootstrap=True, criterion=gini, max_depth=None, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=100; total time=   0.0s
[CV] END bootstrap=True, criterion=gini, max_depth=None, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=50; total time=   0.0s
[CV] END bootstrap=True, criterion=gini, max_depth=None, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=100; total time=   0.0s
[CV] END bootstrap=True, criterion=gini, max_depth=None, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=50; total time=   0.0s
[CV] END bootstrap=True, criterion=gini, max_depth=None, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=200; total time=   0.0s
[CV] END bootstrap=True, criterion=gini, max_depth=None, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=200; total time=   0.0s
[CV] END boo

/Users/junlo/Documents/Py Programs/myenv/lib/python3.11/site-packages/sklearn/model_selection/_validation.py:425: FitFailedWarning: 
3840 fits failed out of a total of 26880.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
2569 fits failed with the following error:
Traceback (most recent call last):
  File "/Users/junlo/Documents/Py Programs/myenv/lib/python3.11/site-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/Users/junlo/Documents/Py Programs/myenv/lib/python3.11/site-packages/sklearn/base.py", line 1144, in wrapper
    estimator._validate_params()
  File "/Users/junlo/Documents/Py Programs/myenv/lib/python3.11/site-packages/sklearn/base.py", li

Random Forest model saved to random_forest_model.joblib
Scaler saved to scaler.joblib
Model Accuracy with Best Parameters: 76.64%


In [8]:
# Read in data 
df = pd.read_csv('Data/new_data_with_predictions.csv')

# Define row color function
def color_row(row):
    color = 'lightgreen' if row['Guess'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Sort by Original ROI column  
df = df.sort_values(by='Original ROI (%)', ascending=False)  

# Filter to top 300 rows
df = df.head(300)

# Filter columns to show
columns = ['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 
           'ROI (%)', 'OTM (%)', 'Guess']
df = df[columns]

# Apply cell and row styling 
styled_df = (df.style
                .applymap(lambda x: 'color: black') # Black text
                .apply(color_row, axis=1) # Color rows
                .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns)) 

# Display styled DataFrame
styled_df